
File: 05-solution.py


Michel Bierlaire

Thu Aug 22 11:48:53 2024



In [ ]:

from IPython.core.display_functions import display
import biogeme.biogeme_logging as blog
from biogeme.biogeme import BIOGEME
from biogeme.expressions import Beta, log, bioDraws, MonteCarlo
from biogeme.models import loglogit, logit
from biogeme.results import compile_estimation_results


Variables used for the specification of the Swissmetro model are defined in the file `swissmetro_variables.py`.

In [ ]:

from swissmetro_variables import (
    database,
    CHOICE,
    TRAIN_AV_SP,
    SM_AV,
    CAR_AV_SP,
    TRAIN_TT_SCALED,
    TRAIN_COST_SCALED,
    TRAIN_HE_SCALED,
    SM_TT_SCALED,
    SM_COST_SCALED,
    SM_HE_SCALED,
    CAR_TT_SCALED,
    CAR_CO_SCALED,
)



The objective of this series of exercises is perform a similar modeling exercise as seen during the lecture.

The starting point is the logit model presented below. Then,

1. estimate a model where the travel time coefficient is normally distributed within the population,
2. compare the results.

**Tip:**<div class="alert alert-block alert-info">It is advised to start working with a low number of draws,
until the script is working well. Then, increase the number of draws to 10000, say. Then, execute the script
overnight.  </div>

In [ ]:
number_of_draws = 10


As the estimation time may be long, we ask Biogeme to report the details of the iterations.

In [ ]:
logger = blog.get_screen_logger(level=blog.INFO)


# Parameters

In [ ]:
asc_car = Beta('asc_car', 0, None, None, 0)
asc_train = Beta('asc_train', 0, None, None, 0)
b_time = Beta('b_time', 0, None, None, 0)
b_cost = Beta('b_cost', 0, None, None, 0)
b_fr = Beta('b_fr', 0, None, None, 0)



# Availability conditions

In [ ]:
av = {1: TRAIN_AV_SP, 2: SM_AV, 3: CAR_AV_SP}



# Logit model

## Utility functions

In [ ]:
V1 = (
    asc_train
    + b_time * TRAIN_TT_SCALED
    + b_cost * TRAIN_COST_SCALED
    + b_fr * TRAIN_HE_SCALED
)
V2 = b_time * SM_TT_SCALED + b_cost * SM_COST_SCALED + b_fr * SM_HE_SCALED
V3 = asc_car + b_time * CAR_TT_SCALED + b_cost * CAR_CO_SCALED
V = {1: V1, 2: V2, 3: V3}



## Model

In [ ]:
logprob = loglogit(V, av, CHOICE)



## Estimation

In [ ]:
biogeme = BIOGEME(database, logprob)
biogeme.modelName = '01logit'
results_logit = biogeme.estimate(recycle=True)



## Results

General statistics.

In [ ]:
print(results_logit.print_general_statistics())


Estimated parameters

In [ ]:
param_logit = results_logit.get_estimated_parameters()
display(param_logit)


Now, specify and estimate a model where the travel time coefficient is normally distributed within the population.
1. Introduce the additional parameters.
2. Specify the utility functions.
3. Specify the choice model to obtain the log likelihood function.
4. Estimate the values of the parameters.
5. Compare the results.